## Hot air balloon - lift calculator
### Box shape
[Source code](https://gitea.citizen4.eu/sp9unb/balloon-calc) 

[Run in mybinder.org IDE](https://mybinder.org/v2/git/https%3A%2F%2Fgitea.citizen4.eu%2Fsp9unb%2Fballoon-calc/HEAD?labpath=work%2Fhotair-box.ipynb) 

In [36]:
# https://pythreejs.readthedocs.io
from pythreejs import *
from IPython.display import HTML,display
from math import pi

# https://ipywidgets.readthedocs.io
import ipywidgets as widgets
from ipywidgets import Layout

# https://pypi.org/project/termcolor/
from termcolor import colored

#from scipy.interpolate import interp1d
#import numpy as np

#math
from math import sin, tan, sqrt

In [37]:
# air density–temperature relationship at 1 atm or 101.325 kPa
# https://en.wikipedia.org/wiki/Density_of_air
# https://www.engineersedge.com/calculators/air-density.htm
# temp in st.C   density in g/m3

#temp = [-25,-20,-15,-10,-5,0,5,10,15,20,25,30,35]
#dens = [1422.4,1394.3,1367.3,1341.3,1316.3,1292.2,1269.0,1246.6,1225.0,1204.1,1183.9,1164.4,1145.5]
#dens_temp_func = interp1d(temp, dens)


def airDensity(temp=0.0):
    tempK = temp + 273.0   # absolute temperature [K]
    p = 101325.0           # pressure [Pa]
    rSpec = 287.0500676    # specific gas constant for dry air [J⋅kg−1⋅K−1]
    return 1000.0 * p / ( rSpec * tempK )

In [40]:
# Ascent rate at ground level
# https://northstar-www.dartmouth.edu/~klynch/pmwiki-gc/uploads/BalloonCalulations.pdf

# Coefficient of Drag assumed to 0.3 (flat top)
Cd = 0.3
g = 9.81 # [m/s2]

def ascentRate(volume=1.0, airDens=1.0, liftForce=1.0, topArea=1.0): 
    val = ( 2 * liftForce * g  ) / ( Cd * airDens * topArea )
    if val < 0.0:
        val = 0.0
    return sqrt( val )


In [41]:
def f(width,height,depth,airTemp,hotAirTemp,coatDens,tapeDens,payloadWeight):
    
  
    out=widgets.Output(layout={'margin': '10px 10px 10px 20px'})   
    with out:    
    # Volume
        volume = width * height * depth
        print( "{:<20}{:>6.1f} [m3]".format("Volume:",volume)) 
    # Area
        area = 2 * (width * height + width * depth + height * depth)
        print( "{:<20}{:>6.1f} [m2]".format("Area:",area))  
    # Coating density (protective film for painting): 300g / 4x5m = 15g/m2       
        coatingWeight = coatDens * area
        print( "{:<20}{:>6.1f} [g]".format("Coating weight:",coatingWeight))   
    # adhesive tape density : average 2g/m   
        tapeLength = 2 * width + 2 * depth + 4 * height
        tapeWeight = tapeDens * tapeLength
        print( "{:<20}{:>6.1f} [m]".format("Adh.tape length:",tapeLength))          
        print( "{:<20}{:>6.1f} [g]".format("Adh.tape weight:",tapeWeight))    
        totalWeight = coatingWeight + tapeWeight
        print( "{:<20}{:>6.1f} [g]".format("Total ball. weight:",totalWeight))
    # Lift per volume g/m3  
    #    airDens = dens_temp_func( airTemp )
    #    hotAirDens = dens_temp_func( hotAirTemp )    
        airDens = airDensity( airTemp )
        hotAirDens = airDensity( hotAirTemp )  
        lift = airDens - hotAirDens
        print( "{:<20}{:>6.1f} [g/m3]".format("Lift/volume:",lift))      
    # Total lift force  lift * volume 
        totalLiftForce = lift * volume
        print( "{:<20}{:>6.1f} [g]".format("Total lift force:",totalLiftForce))    
    # Free lift force totalLiftForce - coatingWeight 
        freeLiftForce = totalLiftForce - totalWeight - payloadWeight
        if freeLiftForce < 0:
            color = 'red'
        else:
            color = None
        print( colored("{:<20}{:>6.1f} [g]".format("Free lift force:",freeLiftForce),color)) 
    # Ascent rate        
        topArea = width * depth
        ascRate = ascentRate(volume, airDens/1000.0, freeLiftForce/1000.0, topArea)
        print( "{:<20}{:>6.1f} [m/s]".format("Ascent rate:",ascRate))  

    geometry=BoxBufferGeometry(
                                width=width, 
                                height=height, 
                                depth=depth,
                                widthSegments=5, 
                                heightSegments=10,
                                depthSegments=15)

    box = Mesh(geometry=geometry,
                material=MeshLambertMaterial(color='gray')
               )
  

# [ width, height, depth ]
    w2 = width/2
    h2 = height/2
    d2 = depth/2
    w2n = -1 * width/2
    h2n = -1 * height/2
    d2n = -1 * depth/2
    tapeGeometry = LineSegmentsGeometry(
        positions=[
            [[w2, h2, d2], [w2, h2n, d2]],
            [[w2, h2, d2], [w2n, h2, d2]],
            [[w2n, h2, d2], [w2n, h2n, d2]], 
            [[w2, h2, d2n], [w2, h2n, d2n]],
            [[w2, h2, d2n], [w2n, h2, d2n]],
            [[w2n, h2,d2n], [w2n, h2n, d2n]], 
            [[w2, h2n,d2], [w2, h2n, d2n]],
            [[w2n, h2n,d2], [w2n, h2n, d2n]]             
        ],
    )        
    tapeMaterial = LineMaterial(linewidth=3, color='#ffffff')    
    tape = LineSegments2( tapeGeometry, tapeMaterial )      
        
    
    keyLight = DirectionalLight(color='white', position=[3, 5, 1], intensity=0.5)

    c = PerspectiveCamera(position=[2, 2, 5], up=[0, 1, 0], children=[keyLight])

    scene = Scene(children=[box, tape, c, AmbientLight(color='#777777')], background=None)

    renderer = Renderer(camera=c,
                        scene=scene,
                        alpha=True,
                        clearOpacity=1.0,
                        clearColor='#62a0ea',
                        controls=[OrbitControls(controlling=c)]
                        )
    
    display(widgets.HBox([renderer, out]))    
#    return renderer


    display(HTML('''<style>
         .widget-hbox  { margin-top: 20px; }
     </style>'''))

layout=Layout(width='500px')
style = {'description_width': 'initial'}
   
width=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=2.0, description='Width [m]:',readout_format='.1f',layout=layout,style=style) 
height=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=2.0, description='Height [m]:',readout_format='.1f',layout=layout,style=style) 
depth=widgets.FloatSlider(min=0.1, max=5.0, step=0.1, value=2.0, description='Depth [m]:',readout_format='.1f',layout=layout,style=style)
airTemp=widgets.FloatSlider(min=-40, max=35, step=1.0, value=10.0, description='Air temp.[°C]:',readout_format='.0f',layout=layout,style=style) 
hotAirTemp=widgets.FloatSlider(min=-40, max=55, step=1.0, value=35.0, description='Hot air temp.[°C]:',readout_format='.0f',layout=layout,style=style)
coatDens=widgets.FloatSlider(min=1, max=50, step=1.0, value=15.0, description='Coating density [g/m2]:',readout_format='.0f',layout=layout,style=style) 
tapeDens=widgets.FloatSlider(min=0.5, max=10, step=0.5, value=2.0, description='Adh. tape density [g/m]:',readout_format='.1f',layout=layout,style=style) 
payloadWeight=widgets.FloatSlider(min=0.0, max=1000.0, step=1, value=0.0, description='Payload weight [g]:',readout_format='.0f',layout=layout,style=style)


w = widgets.interactive_output(f, {
                                    'width' : width,
                                    'height' : height,
                                    'depth' : depth,
                                    'airTemp' : airTemp,
                                    'hotAirTemp' : hotAirTemp,
                                    'coatDens' : coatDens,
                                    'tapeDens' : tapeDens,
                                    'payloadWeight' : payloadWeight
                                }
                            )


widgets.VBox([width, height, depth, airTemp, hotAirTemp, coatDens, tapeDens, payloadWeight, w])
